# RNNs

Y'all punks can get the data from kaggle here: https://www.kaggle.com/uciml/sms-spam-collection-dataset/kernels 

In [1]:
import pandas as pd
import numpy as np

df = pd.read_csv('data/spam.csv', encoding = 'latin1')

In [2]:
df.head()

v1                                                 v2 Unnamed: 2  \
0   ham  Go until jurong point, crazy.. Available only ...        NaN   
1   ham                      Ok lar... Joking wif u oni...        NaN   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...        NaN   
3   ham  U dun say so early hor... U c already then say...        NaN   
4   ham  Nah I don't think he goes to usf, he lives aro...        NaN   

  Unnamed: 3 Unnamed: 4  
0        NaN        NaN  
1        NaN        NaN  
2        NaN        NaN  
3        NaN        NaN  
4        NaN        NaN

In [3]:
from html import parser

# Drop the empty columns
df = df.drop(["Unnamed: 2", "Unnamed: 3", "Unnamed: 4"], axis=1)

# Rename the columns
df = df.rename(index=str, columns={"v1": "classification", "v2": "message"})

# Remove HTML encodings
df['message'] = df['message'].apply(parser.unescape)
df.head()

classification                                            message
0            ham  Go until jurong point, crazy.. Available only ...
1            ham                      Ok lar... Joking wif u oni...
2           spam  Free entry in 2 a wkly comp to win FA Cup fina...
3            ham  U dun say so early hor... U c already then say...
4            ham  Nah I don't think he goes to usf, he lives aro...

In [4]:
df['classification'] = pd.get_dummies(df['classification'])

In [5]:
print(df.head())

   classification                                            message
0               1  Go until jurong point, crazy.. Available only ...
1               1                      Ok lar... Joking wif u oni...
2               0  Free entry in 2 a wkly comp to win FA Cup fina...
3               1  U dun say so early hor... U c already then say...
4               1  Nah I don't think he goes to usf, he lives aro...


In [6]:
y = np.array(df['classification'].values.astype(np.int))
np.unique(y)

array([0, 1])

In [7]:
import keras


y = np.array(df['classification'].values)
X = df['message'].values
#print(X)

#y = [0 if y_ == "spam" else 1 for y_ in y]
y_ohe = keras.utils.to_categorical(y)
y_ohe


Using TensorFlow backend.


array([[ 0.,  1.],
       [ 0.,  1.],
       [ 1.,  0.],
       ..., 
       [ 0.,  1.],
       [ 0.,  1.],
       [ 0.,  1.]])

We need to find how long our longest message is

In [8]:
max = 0
count = 0
for i in X:
    if len(i) > max:
        #if len(i) < 200:
        max = len(i)
        #else:
            #count +=1
        
print(max)
print(count)

910
0


In [9]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
NUM_TOP_WORDS = None

tokenizer = Tokenizer(num_words=NUM_TOP_WORDS)
tokenizer.fit_on_texts(X)
word_index = tokenizer.word_index

sequences = tokenizer.texts_to_sequences(X)
sequences = pad_sequences(sequences)
MAX_TEXT_LEN = len(sequences[0])
print(MAX_TEXT_LEN)

189


In [10]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(
    sequences, y, test_size=0.2, stratify=y, random_state=42)

max_text_length = 189

NUM_CLASSES = 1

In [11]:
EMBED_SIZE = 100
# the embed size should match the file you load glove from
embeddings_index = {}
f = open('data/glove.6B/glove.6B.100d.txt', encoding="utf8")
# save key/array pairs of the embeddings
#  the key of the dictionary is the word, the array is the embedding
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()

print('Found %s word vectors.' % len(embeddings_index))

# now fill in the matrix, using the ordering from the
#  keras word tokenizer from before
embedding_matrix = np.zeros((len(word_index) + 1, EMBED_SIZE))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector

print(embedding_matrix.shape)

Found 400000 word vectors.
(8920, 100)


In [12]:
from keras.layers import Embedding

# GRU RNN

In [18]:
from keras.models import Input, Model
from keras.layers import Dense, GRU,LSTM, Activation
from keras.regularizers import l2


In [134]:
from keras.models import Input, Model
from keras.layers import Dense, GRU, Activation
from keras.regularizers import l2

l2_lambda = 0.0001

input_holder = Input(shape=(189,))
embedding_layer = Embedding(len(word_index) + 1,
                            EMBED_SIZE,
                            weights=[embedding_matrix],
                            input_length=MAX_TEXT_LEN,
                            trainable=False)(input_holder)

gru_layer = GRU(100,dropout=0.2, recurrent_dropout=0.2)(embedding_layer)
dense1 = Dense(NUM_CLASSES, 
                activation='sigmoid',
                kernel_initializer='glorot_uniform',
                kernel_regularizer=l2(l2_lambda)
             )(gru_layer)

rnn_gru = Model(inputs=input_holder, outputs=dense1)
rnn_gru.compile(loss='binary_crossentropy', 
              optimizer='rmsprop', 
              metrics=['accuracy'])
print(rnn_gru.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_21 (InputLayer)        (None, 189)               0         
_________________________________________________________________
embedding_22 (Embedding)     (None, 189, 100)          892000    
_________________________________________________________________
gru_2 (GRU)                  (None, 100)               60300     
_________________________________________________________________
dense_18 (Dense)             (None, 1)                 101       
Total params: 952,401
Trainable params: 60,401
Non-trainable params: 892,000
_________________________________________________________________
None


In [135]:
rnn_gru.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=3, batch_size=64)

Train on 4457 samples, validate on 1115 samples
Epoch 1/3
4457/4457 [==============================] - 18s - loss: 0.2159 - acc: 0.9096 - val_loss: 0.1078 - val_acc: 0.9623
Epoch 2/3
4457/4457 [==============================] - 16s - loss: 0.1011 - acc: 0.9650 - val_loss: 0.0882 - val_acc: 0.9722
Epoch 3/3
4457/4457 [==============================] - 16s - loss: 0.0842 - acc: 0.9731 - val_loss: 0.0798 - val_acc: 0.9758


In [137]:
yhat_gru = np.round(rnn_gru.predict(X_test, verbose=1))

1115/1115 [==============================] - 2s     


In [33]:
from sklearn import metrics as mt
rec = mt.recall_score(y_test,yhat_gru)
acc = mt.accuracy_score(y_test,yhat_gru)
print(rec)
print(acc)

NameError: name 'yhat_gru' is not defined

# LSTM RNN

In [129]:
from keras.models import Input, Model
from keras.layers import Dense, LSTM, Activation
from keras.regularizers import l2

l2_lambda = 0.0001

input_holder = Input(shape=(189,))
embedding_layer = Embedding(len(word_index) + 1,
                            EMBED_SIZE,
                            weights=[embedding_matrix],
                            input_length=MAX_TEXT_LEN,
                            trainable=False)(input_holder)

lstm_layer = LSTM(100,dropout=0.2, recurrent_dropout=0.2)(embedding_layer)
dense1 = Dense(NUM_CLASSES, 
                activation='sigmoid',
                kernel_initializer='glorot_uniform',
                kernel_regularizer=l2(l2_lambda)
             )(lstm_layer)

rnn_lstm = Model(inputs=input_holder, outputs=dense1)
rnn_lstm.compile(loss='binary_crossentropy', 
              optimizer='rmsprop', 
              metrics=['accuracy'])
print(rnn_lstm.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_20 (InputLayer)        (None, 189)               0         
_________________________________________________________________
embedding_21 (Embedding)     (None, 189, 100)          892000    
_________________________________________________________________
lstm_21 (LSTM)               (None, 100)               80400     
_________________________________________________________________
dense_17 (Dense)             (None, 1)                 101       
Total params: 972,501
Trainable params: 80,501
Non-trainable params: 892,000
_________________________________________________________________
None


In [130]:
rnn_lstm.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=3, batch_size=64)

Train on 4457 samples, validate on 1115 samples
Epoch 1/3
4457/4457 [==============================] - 22s - loss: 0.1926 - acc: 0.9242 - val_loss: 0.1238 - val_acc: 0.9614
Epoch 2/3
4457/4457 [==============================] - 20s - loss: 0.1071 - acc: 0.9628 - val_loss: 0.0883 - val_acc: 0.9740
Epoch 3/3
4457/4457 [==============================] - 20s - loss: 0.0908 - acc: 0.9686 - val_loss: 0.0833 - val_acc: 0.9722


In [131]:
yhat = np.round(rnn_lstm.predict(X_test, verbose=1))

1115/1115 [==============================] - 3s     


In [132]:
from sklearn import metrics as mt
rec = mt.recall_score(y_test,yhat)
acc = mt.accuracy_score(y_test,yhat)
print(rec)
print(acc)

0.993788819876
0.972197309417


In [144]:
import os
import numpy as np
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils.np_utils import to_categorical
from keras.layers import Dense, Input, Flatten
from keras.layers import Conv1D, MaxPooling1D, Embedding
from keras.models import Model
import sys
import pandas as pd
import pickle
from keras.models import load_model

np.random.seed(1337)

BASE_DIR = ''
GLOVE_DIR = 'data/glove'
MAX_SEQUENCE_LENGTH = 189
MAX_NB_WORDS = 20000
EMBEDDING_DIM = 100
VALIDATION_SPLIT = 0.2



embeddings_index = {}
labels_index = {}  # dictionary mapping label news_group to numeric id
labels = y  # list of label ids


tokenizer = Tokenizer(num_words=NUM_TOP_WORDS)
tokenizer.fit_on_texts(X)
pickle.dump(tokenizer, open('data/tokenizer.004.p', 'wb'))
sequences = tokenizer.texts_to_sequences(X)

word_index = tokenizer.word_index
print('Found %s unique tokens.' % len(word_index))
data = pad_sequences(sequences, maxlen=MAX_SEQUENCE_LENGTH)
labels = to_categorical(np.asarray(labels))
print('Shape of data tensor:', data.shape)
print('Sample data tensor:', data[0, 0:])
print('Shape of label tensor:', labels.shape)
print('Sample label tensor:', labels[690:750, 0:])

# split the data into a training set and a validation set
indices = np.arange(data.shape[0])
np.random.shuffle(indices)
data = data[indices]
labels = labels[indices]
nb_validation_samples = int(VALIDATION_SPLIT * data.shape[0])

x_train = data[:-nb_validation_samples]
y_train = labels[:-nb_validation_samples]
x_val = data[-nb_validation_samples:]
y_val = labels[-nb_validation_samples:]

# prepare embedding matrix
nb_words = min(MAX_NB_WORDS, len(word_index))
embedding_matrix = np.zeros((nb_words + 1, EMBEDDING_DIM))
for word, i in word_index.items():
    if i > MAX_NB_WORDS:
        continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector

embedding_layer = Embedding(nb_words + 1,
                            EMBEDDING_DIM,
                            weights=[embedding_matrix],
                            input_length=MAX_SEQUENCE_LENGTH,
                            trainable=False)        

Found 8919 unique tokens.
Shape of data tensor: (5572, 189)
Sample data tensor: [   0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0   48  466 4409  838  748  654   62    8 1321   87  119
  346 13

In [151]:
l2_lambda = 0.0001

input_holder = Input(shape=(189,))
embedding_layer = Embedding(len(word_index) + 1,
                            EMBED_SIZE,
                            weights=[embedding_matrix],
                            input_length=MAX_TEXT_LEN,
                            trainable=False)(input_holder)

lstm_layer = LSTM(100,dropout=0.2, recurrent_dropout=0.2)(embedding_layer)
dense1 = Dense(2, 
                activation='sigmoid',
                kernel_initializer='glorot_uniform',
                kernel_regularizer=l2(l2_lambda)
             )(lstm_layer)

rnn_lstm = Model(inputs=input_holder, outputs=dense1)
rnn_lstm.compile(loss='binary_crossentropy', 
              optimizer='rmsprop', 
              metrics=['accuracy'])
rnn_lstm.fit(x_train, y_train, validation_data=(x_val, y_val), epochs=3, batch_size=64)

Train on 4458 samples, validate on 1114 samples
Epoch 1/3
4458/4458 [==============================] - 22s - loss: 0.4202 - acc: 0.8596 - val_loss: 0.3857 - val_acc: 0.8707
Epoch 2/3
4458/4458 [==============================] - 20s - loss: 0.3988 - acc: 0.8647 - val_loss: 0.4004 - val_acc: 0.8707
Epoch 3/3
4458/4458 [==============================] - 20s - loss: 0.3980 - acc: 0.8647 - val_loss: 0.3855 - val_acc: 0.8707


In [153]:
for a in embedding_matrix:
    print(a)

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

...

  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.

  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0

# GridSearch

In [27]:
def gs_make_lstm(l2_lambda=0.0001, dropout=0.2, recurrent_dropout=0.2, activation='sigmoid', kernel_initializer='glorot_uniform'):
    print("l2:", l2_lambda, ", dropout:", dropout, ", r_dropout:", recurrent_dropout, "\n")
    input_holder = Input(shape=(189,))
    embedding_layer = Embedding(len(word_index) + 1,
                                EMBED_SIZE,
                                weights=[embedding_matrix],
                                input_length=MAX_TEXT_LEN,
                                trainable=False)(input_holder)

    lstm_layer = LSTM(100,dropout=dropout, recurrent_dropout=recurrent_dropout)(embedding_layer)
    dense1 = Dense(NUM_CLASSES, 
                    activation=activation,
                    kernel_initializer=kernel_initializer,
                    kernel_regularizer=l2(l2_lambda)
                 )(lstm_layer)

    rnn_lstm_gs = Model(inputs=input_holder, outputs=dense1)
    rnn_lstm_gs.compile(loss='binary_crossentropy', 
                  optimizer='rmsprop', 
                  metrics=['accuracy'])
    return rnn_lstm_gs

In [14]:
from keras.wrappers.scikit_learn import KerasClassifier

In [20]:

#LSTM
model = KerasClassifier(build_fn=gs_make_lstm)
param_grid = {
              'l2_lambda':[0.000001,0.0001,0.01], 
              'dropout':[0.1,0.2,0.3], 
              'recurrent_dropout':[0.1,0.2,0.3], 
              'activation':['sigmoid', 'relu'],
             }
# param_grid = {'epochs':[2], 
#               'l2_lambda':[0.000001,0.0001,0.01], 
#               'dropout':[0.1,0.2,0.3], 
#               'recurrent_dropout':[0.1,0.2,0.3], 
#               'activation':['sigmoid', 'relu'], 
#               'kernel_initializer':['glorot_uniform','he_normal']
#              }
grid = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid.fit(X_train, y_train, validation_data=(X_test, y_test), verbose=1)

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 29s - loss: 0.1702 - acc: 0.9418 - val_loss: 0.1043 - val_acc: 0.9614
Epoch 2/2
2971/2971 [==============================] - 7s     
Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 30s - loss: 0.1696 - acc: 0.9334 - val_loss: 0.1015 - val_acc: 0.9659
Epoch 2/2
2971/2971 [==============================] - 7s     
Train on 2972 samples, validate on 1115 samples
Epoch 1/2
2972/2972 [==============================] - 30s - loss: 0.1714 - acc: 0.9371 - val_loss: 0.0914 - val_acc: 0.9686
Epoch 2/2
2972/2972 [==============================] - 7s     
Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 30s - loss: 0.1953 - acc: 0.9337 - val_loss: 0.1365 - val_acc: 0.9561
Epoch 2/2
2971/2971 [==============================] - 7s     
Train on 2971 samples, validate on 1115 samples
Epoch 1/

In [26]:
grid.best_params_

{'activation': 'sigmoid',
 'dropout': 0.1,
 'epochs': 2,
 'kernel_initializer': 'glorot_uniform',
 'l2_lambda': 0.01,
 'recurrent_dropout': 0.1}

In [30]:
#LSTM
model = KerasClassifier(build_fn=gs_make_lstm)
param_grid = {'epochs':[2],
              'l2_lambda':[0.0001,0.01], 
              'dropout':[0.1,0.2,0.3], 
              'recurrent_dropout':[0.1,0.2,0.3]
             }
# param_grid = {'epochs':[2], 
#               'l2_lambda':[0.000001,0.0001,0.01], 
#               'dropout':[0.1,0.2,0.3], 
#               'recurrent_dropout':[0.1,0.2,0.3], 
#               'activation':['sigmoid', 'relu'], 
#               'kernel_initializer':['glorot_uniform','he_normal']
#              }
grid2 = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid2.fit(X_train, y_train, validation_data=(X_test, y_test), verbose=1)

l2: 0.0001 , dropout: 0.1 , r_dropout: 0.1 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 30s - loss: 0.1836 - acc: 0.9313 - val_loss: 0.1243 - val_acc: 0.9623
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.1 , r_dropout: 0.1 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 31s - loss: 0.1672 - acc: 0.9451 - val_loss: 0.0930 - val_acc: 0.9713
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.1 , r_dropout: 0.1 

Train on 2972 samples, validate on 1115 samples
Epoch 1/2
2972/2972 [==============================] - 31s - loss: 0.1645 - acc: 0.9445 - val_loss: 0.0989 - val_acc: 0.9668
Epoch 2/2
2972/2972 [==============================] - 7s     
l2: 0.0001 , dropout: 0.1 , r_dropout: 0.2 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 31s - los

2971/2971 [==============================] - 33s - loss: 0.1767 - acc: 0.9387 - val_loss: 0.0960 - val_acc: 0.9668
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.2 , r_dropout: 0.1 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 33s - loss: 0.1847 - acc: 0.9327 - val_loss: 0.1025 - val_acc: 0.9695
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.2 , r_dropout: 0.1 

Train on 2972 samples, validate on 1115 samples
Epoch 1/2
2972/2972 [==============================] - 33s - loss: 0.1916 - acc: 0.9307 - val_loss: 0.1093 - val_acc: 0.9659
Epoch 2/2
2972/2972 [==============================] - 7s     
l2: 0.0001 , dropout: 0.2 , r_dropout: 0.2 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 33s - loss: 0.1758 - acc: 0.9377 - val_loss: 0.0939 - val_acc: 0.9713
Epoch 2/2
2971/2971 [=====================

2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.3 , r_dropout: 0.1 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 36s - loss: 0.1831 - acc: 0.9337 - val_loss: 0.1107 - val_acc: 0.9659
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.3 , r_dropout: 0.1 

Train on 2972 samples, validate on 1115 samples
Epoch 1/2
2972/2972 [==============================] - 34s - loss: 0.1724 - acc: 0.9391 - val_loss: 0.0928 - val_acc: 0.9722
Epoch 2/2
2972/2972 [==============================] - 7s     
l2: 0.0001 , dropout: 0.3 , r_dropout: 0.2 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2971/2971 [==============================] - 35s - loss: 0.1860 - acc: 0.9283 - val_loss: 0.0958 - val_acc: 0.9695
Epoch 2/2
2971/2971 [==============================] - 7s     
l2: 0.0001 , dropout: 0.3 , r_dropout: 0.2 

Train on 2971 samples, validate on 1115 samples
Epoch 1/2
2

In [34]:
l2s = [0.000001,0.0001,0.01]
dropouts = [0.1,0.2,0.3]
r_dropouts = [0.1,0.2,0.3]

for l2_lambda in l2s:
    for dropout in dropouts:
        for recurrent_dropout in r_dropouts:
            print("\nl2:", l2_lambda, ", dropout:", dropout, ", recurrent_dropout", recurrent_dropout)
            
            input_holder = Input(shape=(189,))
            embedding_layer = Embedding(len(word_index) + 1,
                                        EMBED_SIZE,
                                        weights=[embedding_matrix],
                                        input_length=MAX_TEXT_LEN,
                                        trainable=False)(input_holder)

            lstm_layer = LSTM(100,dropout=dropout, recurrent_dropout=recurrent_dropout)(embedding_layer)
            dense1 = Dense(NUM_CLASSES, 
                            activation='sigmoid',
                            kernel_initializer='glorot_uniform',
                            kernel_regularizer=l2(l2_lambda)
                         )(lstm_layer)

            rnn_lstm = Model(inputs=input_holder, outputs=dense1)
            rnn_lstm.compile(loss='binary_crossentropy', 
                          optimizer='rmsprop', 
                          metrics=['accuracy'])
            rnn_lstm.fit(X_train, y_train, epochs=2, batch_size=64)
            yhat = np.round(rnn_lstm.predict(X_test, verbose=1))
            
            prec = mt.precision_score(y_test,yhat)
            acc = mt.accuracy_score(y_test,yhat)
            print("Precision:", prec)
            print("Accuracy:", acc)
            


l2: 1e-06 , dropout: 0.1 , recurrent_dropout 0.1
Epoch 1/2
4457/4457 [==============================] - 25s - loss: 0.1746 - acc: 0.9336    
Epoch 2/2
1115/1115 [==============================] - 5s     
Precision: 0.981519507187
Accuracy: 0.974887892377

l2: 1e-06 , dropout: 0.1 , recurrent_dropout 0.2
Epoch 1/2
4457/4457 [==============================] - 25s - loss: 0.1775 - acc: 0.9343    
Epoch 2/2
1115/1115 [==============================] - 6s     
Precision: 0.992399565689
Accuracy: 0.947085201794

l2: 1e-06 , dropout: 0.1 , recurrent_dropout 0.3
Epoch 1/2
4457/4457 [==============================] - 26s - loss: 0.1769 - acc: 0.9365    
Epoch 2/2
1115/1115 [==============================] - 6s     
Precision: 0.968718466196
Accuracy: 0.966816143498

l2: 1e-06 , dropout: 0.2 , recurrent_dropout 0.1
Epoch 1/2
4457/4457 [==============================] - 25s - loss: 0.1821 - acc: 0.9331    
Epoch 2/2
1115/1115 [==============================] - 6s     
Precision: 0.983350676379
A

KeyboardInterrupt: 

In [32]:
grid2.best_params_

{'activation': 'sigmoid',
 'dropout': 0.1,
 'epochs': 2,
 'l2_lambda': 0.0001,
 'recurrent_dropout': 0.3}